In [121]:
import pandas as pd
pd.options.plotting.backend = "plotly" #interactive plots will be useful in this context
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import gensim
from sentence_transformers import SentenceTransformer, util
import pickle
import torch
from sklearn.cluster import KMeans
from nltk.corpus import stopwords
stop_words = set(stopwords.words('english'))

In [36]:
df_r=pd.read_csv('../datasets/df_k31_k39.csv')
k39_umap = pickle.load(open('../Model_Selection/k_39_umap', 'rb'))
k39_full = pickle.load(open('../Model_Selection/k_39_full', 'rb'))
k31_umap = pickle.load(open('../Model_Selection/k_31_umap', 'rb'))
k31_full = pickle.load(open('../Model_Selection/k_31_full', 'rb'))

In [120]:
list_of_vec = []
job_list = []
for index, row in df_r.iterrows():
    job = row['url']
    if job not in job_list:
        job_list.append(job)
        
        df_r_job = df_r[df_r.url == row['url']]
    
        
        cluster_list = []
        cluster_vec = []

        for i, row_r in df_r_job.iterrows():
            cluster = row_r['cluster_k31_full']
            if cluster not in cluster_list:
                cluster_list.append(cluster)
        for i in range(0,31):
            if(i in cluster_list):
                cluster_vec.append(1)
            else:
                cluster_vec.append(0)
        list_of_vec.append(cluster_vec)

cols = []
for i in range(0,31):
    cols.append(str(i))
df_clusters = pd.DataFrame(list_of_vec, columns = cols)
df_c = pd.concat([df, df_clusters], axis=1)

In [74]:
from collections import Counter
def get_bigrams(requirement_list):
    list = []
    for requirement in requirement_list:
        for word in requirement.split():
            word = word.lower()
            if (len(word) >1) & (word not in stop_words):
                list.append(word)
    
    bigrams = zip(list,list[1:])
    #print(list)
    bigrams_count = Counter(bigrams)
    return(bigrams_count)

In [172]:
def get_label(cluster):#model needs to be incorperated if plotting different models
    df_r_cluster = df_r[df_r.cluster_k39_full == cluster]
    cluster_requirement_list = []
    for i, row in df_r_cluster.iterrows():
        cluster_requirement_list.append(row['requirement'])
    tuple = get_bigrams(cluster_requirement_list).most_common(3)
    label = ""
    for bigram in range(3):   
        for word in tuple[bigram][0]:
            label+=word+" "
        label=label[:-1]
        label+=", "
    label = label[:-2]
    label = label.replace(",,",",")
    label = "Cluster "+str(cluster)+": "+label
    return(label)
get_label(1)
df_c[str(1)].mean()

0.23756906077348067

In [187]:
x = []
y = []
for i in range(0,len(k31_full.cluster_centers_)):
    y.append(get_label(i))
    x.append(df_c[str(i)].mean())
sorted = list(zip(x,y))
sorted.sort()
x=[]
y=[]
for tuple in sorted:
    x.append(tuple[0])
    y.append(tuple[1])

fig = go.Figure([go.Bar(x=x, y=y,orientation='h')])
fig.update_layout(height=900, title = '3 most common bigrams of each cluster and relative cluster precense in job postings',barmode='stack')
fig.show()

In [141]:
print(y.sort())

None


In [15]:
df_r.head()

Unnamed: 0  Unnamed: 0.1  \
0           0             0   
1           1             1   
2           2             2   
3           3             3   
4           4             4   

                                     requirement_raw  \
0  Collaborate with stakeholders and other engine...   
1  \nApply the right tools for the job and solve ...   
2  \nDevelop knowledge representations and virtua...   
3  \nProvide model explanations and apply structu...   
4  \nLearn desired behavior from examples using c...   

                               requirement_tokenized  Unnamed: 0.1.1  \
0  ['collaborate', 'with', 'stakeholders', 'and',...               0   
1  ['apply', 'the', 'right', 'tools', 'for', 'the...               0   
2  ['develop', 'knowledge', 'representations', 'a...               0   
3  ['provide', 'model', 'explanations', 'and', 'a...               0   
4  ['learn', 'desired', 'behavior', 'from', 'exam...               0   

                           dt  \
0  2021-08-08 21:01:03.303868   
1  2021-08-08 21:01:03.303868   
2  2021-08-08 21:01:03.303868   
3  2021-08-08 21:01:03.303868   
4  2021-08-08 21:01:03.303868   

                                                 url            title  \
0  https://se.indeed.com/viewjob?jk=b0669075c820856d  Data Scientist    
1  https://se.indeed.com/viewjob?jk=b0669075c820856d  Data Scientist    
2  https://se.indeed.com/viewjob?jk=b0669075c820856d  Data Scientist    
3  https://se.indeed.com/viewjob?jk=b0669075c820856d  Data Scientist    
4  https://se.indeed.com/viewjob?jk=b0669075c820856d  Data Scientist    

           location country  ... cluster_k39_umap cluster_k39_umap_str  \
0   Jobba hemifrån       se  ...               30                   30   
1   Jobba hemifrån       se  ...                6                    6   
2   Jobba hemifrån       se  ...                5                    5   
3   Jobba hemifrån       se  ...               30                   30   
4   Jobba hemifrån       se  ...               38                   38   

   cluster_k39_full cluster_k39_full_str  cluster_k31_umap  \
0                16                   16                30   
1                25                   25                15   
2                 6                    6                 5   
3                19                   19                30   
4                 9                    9                28   

   cluster_k31_umap_str  cluster_k31_full  cluster_k31_full_str  \
0                    30                16                    16   
1                    15                25                    25   
2                     5                 6                     6   
3                    30                19                    19   
4                    28                 9                     9   

                              embedding_umap  \
0     [8.437570571899414, 1.452495813369751]   
1     [9.287023544311523, 1.903634786605835]   
2   [12.255410194396973, 0.6413768529891968]   
3     [8.778813362121582, 1.796252727508545]   
4  [12.108744621276855, 0.36008894443511963]   

                                     embedding_sbert  
0  [ 2.92994883e-02 -2.01876592e-02 -1.77986640e-...  
1  [ 5.18322783e-03 -2.73219533e-02  1.39794778e-...  
2  [-2.55110599e-02 -4.51361351e-02  2.83039957e-...  
3  [ 7.65320137e-02  3.38071585e-02  1.26707423e-...  
4  [-1.26626417e-02 -2.44116709e-02 -1.78283397e-...  

[5 rows x 24 columns]

In [16]:
umap = df_r['embedding_umap'].tolist()
umap1 = []
umap2 = []
for i in umap:
    umap1.append(float(i.split(',')[0].split('[')[1]))
    umap2.append(float(i.split(',')[1].split(']')[0]))
df_r['umap1']=umap1
df_r['umap2']=umap2

In [33]:
fig = px.scatter(df_r,'umap1','umap2', hover_data = ['requirement'], title = "UMAP Analysis of job requirements embeddings from all_distilroberta_v1", color = 'k_5')
fig.update_traces(marker=dict(size=1.5))
fig.show()

ValueError: Value of 'x' is not the name of a column in 'data_frame'. Expected one of ['Unnamed: 0', 'requirement_raw', 'requirement_tokenized', 'Unnamed: 0.1.1', 'dt', 'url', 'title', 'location', 'country', 'full_text', 'list_elements', 'row_id', 'requirement', 'cluster_dbscan_all_MiniLM_L12_v2', 'full_set_row_id', 'k_25', 'k_15', 'k_5'] but received: umap1

In [67]:
fig = px.scatter(df_r,'umap1','umap2', hover_data = ['requirement'], title = "UMAP Analysis of job requirements embeddings from all_distilroberta_v1", color = 'cluster_k39_umap_str')
fig.update_traces(marker=dict(size=1.5))
fig.show()

In [19]:
df_c.head()

Unnamed: 0                          dt  \
0           0  2021-08-08 21:01:03.303868   
1           1  2021-08-08 21:01:09.824428   
2           2  2021-08-08 21:01:18.030788   
3           3  2021-08-08 21:01:20.651507   
4           4  2021-08-08 21:01:27.135797   

                                                 url  \
0  https://se.indeed.com/viewjob?jk=b0669075c820856d   
1  https://se.indeed.com/viewjob?jk=dbfe7d7c087065d7   
2  https://se.indeed.com/viewjob?jk=841a8fdd1bb00f2f   
3  https://se.indeed.com/viewjob?jk=88c25a48d2da8a7a   
4  https://se.indeed.com/viewjob?jk=1b4b8ee005f06350   

                              title            location country  \
0                   Data Scientist      Jobba hemifrån       se   
1  Data Scientist, Search Insights           Stockholm       se   
2            Junior data scientist     411 21 Göteborg       se   
3                   Data Scientist    118 72 Stockholm       se   
4                   Data Scientist               Solna       se   

                                           full_text  \
0  About us\n\nHere at Mavenoid, we are building ...   
1  Data, Research & Insights\nData Science\nThe P...   
2  Utilifeed is a rapidly expanding startup with ...   
3  AI Data scientistLocation: Stockholm, SwedenDi...   
4  Currently, we are looking for a talented data ...   

                                       list_elements  0  1  ...  21  22  23  \
0  ['Collaborate with stakeholders and other engi...  0  0  ...   1   1   0   
1  ['\nExperimentation strategy including AB test...  0  0  ...   1   0   1   
2  ['\nImproving pour data ingestion pipeline, we...  0  1  ...   0   0   1   
3  ['Proven experience in Machine Learning (ML) a...  1  0  ...   0   1   0   
4  ['\nYou have a start-up mentality, with delive...  1  0  ...   1   0   0   

   24  25  26  27  28  29  30  
0   1   1   0   0   0   0   0  
1   0   0   1   0   0   0   0  
2   0   0   0   1   0   1   0  
3   0   0   1   0   0   0   1  
4   0   1   1   1   0   0   1  

[5 rows x 39 columns]

In [70]:
len(df_c)

2633